# Strategia in tempo reale SU IBKR: SMA su 50 e 200 minuti

In [1]:
from ib_insync import * 
import pandas as pd
import numpy as np
import datetime as dt
from IPython.display import display, clear_output
util.startLoop()

In [2]:
ib = IB()
ib.connect()

<IB connected to 127.0.0.1:7497 clientId=1>

<font color=RED><b><font size=+2>Il mercato deve essere aperto!!!

In [ ]:
# parameteri
sma_s = 50
sma_l = 200
freq = "1 min"
units = 10000
contract = Forex('EURUSD') # usiamo questo per ottenere i dati
ib.qualifyContracts(contract)
cfd = CFD("EUR", currency = "USD") # usiamo questo per fare trading
ib.qualifyContracts(cfd)
conID = cfd.conId

In [ ]:
# Esiste?
conID

In [ ]:
def onBarUpdate(bars, hasNewBar):  
    global df, last_bar
    
    if bars[-1].date > last_bar: 
        last_bar = bars[-1].date
    
        df = pd.DataFrame(bars)[["date", "open", "high", "low", "close"]].iloc[:-1] 
        df.set_index("date", inplace = True)
        
        ######
        df = df[["close"]].copy() # per togliere le altre info
        df["sma_s"] = df.close.rolling(sma_s).mean()
        df["sma_l"] = df.close.rolling(sma_l).mean()
        df.dropna(inplace = True)
        df["position"] = np.where(df["sma_s"] > df["sma_l"], 1, -1 )
        ######
        
        # Facciamo qui il trading
        target = df["position"][-1] * units
        execute_trade(target = target)
        
        # qui mostriamo il df
        clear_output(wait=True)
        display(df)

def execute_trade(target):
    global current_pos
    try:
        current_pos = [pos.position for pos in ib.positions() if pos.contract.conId == conID][0]
    except:
        current_pos = 0 # nel caso non ci sia perché abbiamo appena iniziato
         
    trades = target - current_pos # quale trade dobbiamo fare
    if trades > 0:
        order = MarketOrder("BUY", abs(trades))
        trade = ib.placeOrder(cfd, order)  
    elif trades < 0:
        order = MarketOrder("SELL", abs(trades))
        trade = ib.placeOrder(cfd, order)

In [ ]:
bars = ib.reqHistoricalData(contract,endDateTime="",durationStr='1 D', # lungo a sufficienza per farci stare la media lunga
        barSizeSetting=freq, whatToShow='MIDPOINT', useRTH=True, formatDate=2, keepUpToDate=True)
last_bar = bars[-1].date
bars.updateEvent += onBarUpdate
# aspettare la prossima fine di minuto

In [ ]:
ib.cancelHistoricalData(bars)

## Monitorare i trade

In [ ]:
ib.fills()

In [ ]:
pd.DataFrame([fs.execution for fs in ib.fills()])[["execId", "time", "side", "cumQty", "avgPrice"]].set_index("execId")

In [ ]:
pd.DataFrame([fs.commissionReport for fs in ib.fills()])[["execId", "realizedPNL"]].set_index("execId")

In [6]:
# parameteri
sma_s = 2
sma_l = 5 # più corti perché voglio vedere tanti trade per testing
freq = "1 min"
units = 1000
contract = Forex('EURUSD') # usiamo questo per ottenere i dati
ib.qualifyContracts(contract)
cfd = CFD("EUR", currency = "USD") # usiamo questo per fare trading
ib.qualifyContracts(cfd)
conID = cfd.conId

In [7]:
def onBarUpdate(bars, hasNewBar):  
    global df, last_bar
    
    if bars[-1].date > last_bar: 
        last_bar = bars[-1].date
    
        df = pd.DataFrame(bars)[["date", "open", "high", "low", "close"]].iloc[:-1] 
        df.set_index("date", inplace = True)
        
        ######
        df = df[["close"]].copy() # per togliere le altre info
        df["sma_s"] = df.close.rolling(sma_s).mean()
        df["sma_l"] = df.close.rolling(sma_l).mean()
        df.dropna(inplace = True)
        df["position"] = np.where(df["sma_s"] > df["sma_l"], 1, -1 )
        ######
        
        # Facciamo qui il trading
        target = df["position"][-1] * units
        execute_trade(target = target)
        
        # qui mostriamo il df
        clear_output(wait=True)
        display(df)
    # NUOVO
    else:
        try:
            trade_reporting() # la eseguiamo ogni tanto, quando non c'è una barra completa, per non disturbare il sistema
        except:
            pass

def execute_trade(target):
    global current_pos
    try:
        current_pos = [pos.position for pos in ib.positions() if pos.contract.conId == conID][0]
    except:
        current_pos = 0 # nel caso non ci sia perché abbiamo appena iniziato
         
    trades = target - current_pos # quale trade dobbiamo fare
    if trades > 0:
        order = MarketOrder("BUY", abs(trades))
        trade = ib.placeOrder(cfd, order)  
    elif trades < 0:
        order = MarketOrder("SELL", abs(trades))
        trade = ib.placeOrder(cfd, order)
        
# NUOVO
def trade_reporting():
    global report
    
    fill_df = pd.DataFrame([fs.execution for fs in ib.fills()])[["execId", "time", "side", "cumQty", "avgPrice"]].set_index("execId")
    profit_df = pd.DataFrame([fs.commissionReport for fs in ib.fills()])[["execId", "realizedPNL"]].set_index("execId")
    report = pd.concat([fill_df, profit_df], axis = 1).set_index("time").loc[session_start:] # session_start:  per evitare di prendere dati di sessioni precedenti
    report = report.groupby("time").agg({"side":"first", "cumQty":"max", "avgPrice":"mean", "realizedPNL":"sum"}) #  aggreghiamo lo stesso trade che potrebbe venire spezzato
    report["cumPNL"] = report.realizedPNL.cumsum()
        
    clear_output(wait=True)
    display(df, report)

In [8]:
session_start = pd.to_datetime(dt.datetime.utcnow()).tz_localize("utc") # session_start:  per evitare di prendere dati di sessioni precedenti
bars = ib.reqHistoricalData(contract, endDateTime='', durationStr='1 D',
        barSizeSetting=freq, whatToShow='MIDPOINT', useRTH=True, formatDate=2, keepUpToDate=True)
last_bar = bars[-1].date
bars.updateEvent += onBarUpdate
# ATTENZIONE che nel report c'è il tempo effettivo del trade e nel df sopra la chiusura delle barre invece

In [ ]:
ib.cancelHistoricalData(bars) 

In [ ]:
# Per fermare la sessione di trading:
# - a un tempo preciso
# - a un limite di guadagno o perdita

In [9]:
from datetime import timedelta
end_time = dt.datetime.utcnow() + timedelta(minutes=10)  
while True:
    ib.sleep(5) 
    if dt.datetime.utcnow() >= end_time: 
        execute_trade(target = 0) # chiudo tutto
        ib.cancelHistoricalData(bars) 
        ib.sleep(10)
        try:
            trade_reporting() 
        except:
            pass
        print("Finito!")
        ib.disconnect()
        break


close     sma_s     sma_l  position
date                                                             
2024-09-29 21:19:00+00:00  1.116085  1.116060  1.116069        -1
2024-09-29 21:20:00+00:00  1.116145  1.116115  1.116097         1
2024-09-29 21:21:00+00:00  1.116030  1.116087  1.116073         1
2024-09-29 21:22:00+00:00  1.116095  1.116062  1.116078        -1
2024-09-29 21:23:00+00:00  1.116130  1.116113  1.116097         1
...                             ...       ...       ...       ...
2024-09-30 14:16:00+00:00  1.116425  1.116400  1.116266         1
2024-09-30 14:17:00+00:00  1.116415  1.116420  1.116340         1
2024-09-30 14:18:00+00:00  1.116265  1.116340  1.116378        -1
2024-09-30 14:19:00+00:00  1.116175  1.116220  1.116331        -1
2024-09-30 14:20:00+00:00  1.116045  1.116110  1.116265        -1

[1022 rows x 4 columns]

side  cumQty  avgPrice  realizedPNL   cumPNL
time                                                                  
2024-09-30 14:12:06+00:00  SLD  1000.0   1.11610      0.00000  0.00000
2024-09-30 14:15:05+00:00  BOT  2000.0   1.11645     -4.35002 -4.35002
2024-09-30 14:19:05+00:00  SLD  2000.0   1.11610     -2.35000 -6.70002
2024-09-30 14:21:12+00:00  BOT  1000.0   1.11605     -1.95000 -8.65002

Finito!
